In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
from utils.metrics import construct_dataframe_faces, construct_dataframe
from utils.imgs import get_bbox_size, subset_exists
import plotly.graph_objects as go
from utils.metrics import get_dataframe_faces
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
from scipy.stats import wasserstein_distance

In [2]:
ggplot_colors = [
    '#F8766D', '#7CAE00', '#00BFC4', '#C77CFF', 
    '#00A9FF', '#FF61CC', '#FF9E7D', '#00BA38', 
    '#619CFF', '#F564E3'
]

In [3]:
def kl_divergence(p, q):
    """
    Calculate the Kullback-Leibler divergence between two distributions.
    
    Parameters:
    p (array-like): The reference distribution
    q (array-like): The distribution to compare against p
    
    Returns:
    float: The KL divergence from q to p
    """
    # Ensure the inputs are numpy arrays
    p = np.asarray(p)
    q = np.asarray(q)
    
    # Normalize the distributions
    p = p / np.sum(p)
    q = q / np.sum(q)
    
    # Avoid division by zero by adding a small epsilon
    epsilon = 1e-10
    
    # Calculate KL divergence
    kl = np.sum(p * np.log((p + epsilon) / (q + epsilon)))
    
    return kl

# Face Analysis
Perform face cosine similarity analysis for two and three people generation


In [4]:
def get_face_analysis(experiments_face_analysis: list, title: str):
    for s in experiments_face_analysis:
        if not subset_exists(s):
            print(f"Subset {s} does not exist")
    df_raw = pd.concat(
        [
            get_dataframe_faces(subset_name)
            for subset_name in experiments_face_analysis
        ],
        axis=0,
    )
    dfs = df_raw.groupby('subset')['similarity_cosine'].agg([
    ('mean', 'mean'),
    ('std', 'std'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
    ])
    fig_box = px.box(df_raw, y="similarity_cosine", x="subset", 
                     template='ggplot2',
                     width=800, height=400)
    fig_box.update_layout(
        yaxis_title="Cosine similarity",
        xaxis_title="Method",
        title=title,
        xaxis=dict(
            title=dict(font=dict(size=16)),
            tickfont=dict(size=14),
            tickmode='array',
            tickvals=[0, 1, 2],  # Position of tick marks
            ticktext=['IPAdapter Plus FaceID v2', 'IPAdapter Plus Face', 'Prompt Alone']  # Labels for tick marks
        ),
        yaxis=dict(
            title=dict(font=dict(size=16)),
            tickfont=dict(size=14),
        )
    )
    return fig_box, dfs, df_raw

In [5]:
experiments_two = [
    "two_people_faceid_dreamshaper",
    "two_people_normalip",
    "base_two_people_dreamshaper+face"
]
experiments_three = [
    "three_people_faceid_dreamshaper",
    "three_people_normalip",
    "base_three_people_dreamshaper+face"
]
fig1, dfs1, df_raw1 = get_face_analysis(experiments_two, title="Cosine similarity per method for two people generation")
fig2, dfs2, df_raw2 = get_face_analysis(experiments_three, title="Cosine similarity per method for three people generation")

fig1.write_image("figures/face_analysis_two_people_box.png")
fig2.write_image("figures/face_analysis_three_people_box.png")

# fig1.show()
# fig2.show()
# 
# display(dfs1)
# display(dfs2)

In [6]:
# ablation
experiments = [
    "two_people_faceid_dreamshaper",
    "two_people_normalip",
    "two_people_faceid_no_facedetailer",
    "two_people_normalip_no_facedetailer",
    "three_people_faceid_dreamshaper",
    "three_people_normalip",
    "three_people_faceid_no_facedetailer",
    "three_people_normalip_no_facedetailer",
]
fig1, dfs1, df_raw1 = get_face_analysis(experiments, title="Cosine similarity per method for two people generation")
# drop rows where subset (index) ends with _diff
# df_raw1['subset'] = df_raw1['subset'].map(rename_dict)
df_raw1.groupby('subset')[['face_quality', 'similarity_cosine']].agg([
    ('mean', 'mean'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
]).round(3)

face_quality        similarity_cosine  \
                                              mean stderr              mean   
subset                                                                        
three_people_faceid_dreamshaper              0.816  0.003             0.559   
three_people_faceid_no_facedetailer          0.751  0.004             0.266   
three_people_normalip                        0.787  0.004             0.421   
three_people_normalip_no_facedetailer        0.740  0.005             0.178   
two_people_faceid_dreamshaper                0.819  0.003             0.577   
two_people_faceid_no_facedetailer            0.769  0.004             0.301   
two_people_normalip                          0.787  0.004             0.459   
two_people_normalip_no_facedetailer          0.766  0.005             0.209   

                                              
                                      stderr  
subset                                        
three_people_faceid_dreamshaper        0.004  
three_people_faceid_no_facedetailer    0.005  
three_people_normalip                  0.004  
three_people_normalip_no_facedetailer  0.003  
two_people_faceid_dreamshaper          0.004  
two_people_faceid_no_facedetailer      0.005  
two_people_normalip                    0.004  
two_people_normalip_no_facedetailer    0.004

In [7]:
df_raw1['n_people'] = 2
df_raw2['n_people'] = 3
rename_dict = {
    'two_people_faceid_dreamshaper': 'IPAdapter Plus FaceID v2',
    'two_people_normalip': 'IPAdapter Plus Face',
    'base_two_people_dreamshaper+face': 'Prompt Alone',
    'base_two_people_dreamshaper+face_newseed': 'Prompt Alone (New Seed)',
    'three_people_faceid_dreamshaper': 'IPAdapter Plus FaceID v2',
    'three_people_normalip': 'IPAdapter Plus Face',
    'base_three_people_dreamshaper+face': 'Prompt Alone',
    'base_three_people_dreamshaper+face_newseed': 'Prompt Alone (New Seed)',
    "two_people_faceid_no_facedetailer": "FaceID No Face Inpaint",
    "three_people_faceid_no_facedetailer": "FaceID No Face Inpaint",
    "two_people_normalip_no_facedetailer": "IPAdapter Plus No Face Inpaint",
    "three_people_normalip_no_facedetailer": "IPAdapter Plus No Face Inpaint",
    "two_people_faceid_no_controlnet": "IPA+ FIDv2 No ControlNet",
    "three_people_faceid_no_controlnet": "IPA+ FIDv2 No ControlNet",
    "two_people_normalip_no_controlnet": "IPA+ Face No ControlNet",
    "three_people_normalip_no_controlnet": "IPA+ Face No ControlNet",
}
df_raw = pd.concat([df_raw1, df_raw2], axis=0)[['subset', 'similarity_cosine', 'n_people']]
df_raw['subset'] = df_raw['subset'].map(rename_dict)

In [8]:
fig = px.box(df_raw, x='subset', y='similarity_cosine', color='n_people', template='ggplot2')
fig.update_layout(
    xaxis_title="Method",
    yaxis_title="Face similarity scores",
    legend_title_text='Number of people',
    width=900,
    height=400,
        legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=0.6,
    ),
    margin=dict(l=20, r=5, t=10, b=10)
)
# increase font size
fig.update_xaxes(title=dict(font=dict(size=16)))
fig.update_yaxes(title=dict(font=dict(size=16)))
fig.update_traces(marker=dict(size=5))
fig.show()
fig.write_image("figures/face_analysis_two_three_people_box.png")

# Face Quality

In [9]:
def get_face_quality(experiments_face_quality: list, title: str):
    for s in experiments_face_quality:
        if not subset_exists(s):
            print(f"Subset {s} does not exist")
    df_raw = pd.concat(
        [
            get_dataframe_faces(subset_name)
            for subset_name in experiments_face_quality
        ],
        axis=0,
    )
    dfs = df_raw.groupby('subset')['face_quality'].agg([
    ('mean', 'mean'),
    ('median', 'median'),
    ('std', 'std'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
    ])
    fig_box = px.box(df_raw, y="face_quality", x="subset", 
                     template='ggplot2',
                     width=800, height=400)
    fig_box.update_layout(
        yaxis_title="Face Quality",
        xaxis_title="Method",
        title=title,
        xaxis=dict(
            title=dict(font=dict(size=16)),
            tickfont=dict(size=14),
            tickmode='array',
            tickvals=[0, 1, 2],  # Position of tick marks
            ticktext=['IPAdapter Plus FaceID v2', 'IPAdapter Plus Face', 'Prompt Alone']  # Labels for tick marks
        ),
        yaxis=dict(
            title=dict(font=dict(size=16)),
            tickfont=dict(size=14),
        )
    )
    return fig_box, dfs, df_raw

In [10]:
experiments_two = [
    "two_people_faceid_dreamshaper",
    "two_people_normalip",
    "two_people_normalip_no_facedetailer",
    "base_two_people_dreamshaper+face",
    "two_people_faceid_no_facedetailer",
]
experiments_three = [
    "three_people_faceid_dreamshaper",
    "three_people_normalip",
    "three_people_normalip_no_facedetailer",
    "base_three_people_dreamshaper+face",
    "three_people_faceid_no_facedetailer",
]
fig1, dfs1, df_raw1 = get_face_quality(experiments_two, title="Face Quality per method for two people generation")
fig2, dfs2, df_raw2 = get_face_quality(experiments_three, title="Face Quality per method for three people generation")

fig1.write_image("face_quality_two_people_box.png")
fig2.write_image("face_quality_three_people_box.png")
df_raw1['n_people'] = 2
df_raw2['n_people'] = 3
df_raw = pd.concat([df_raw1, df_raw2], axis=0)
df_raw['subset'] = df_raw['subset'].map(rename_dict)
df_raw = df_raw[['subset', 'face_quality', 'n_people', 'yaw']]
df_raw.groupby(['n_people', 'subset'])['face_quality'].agg([
    ('mean', 'mean'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
]).round(3)
# df_raw['yaw_abs'] = df_raw['yaw'].abs()
fig = px.box(df_raw, x='subset', y='face_quality', template='ggplot2')
fig.update_layout(
    xaxis_title="Method",
    yaxis_title="Face quality scores",
    width=800,
    height=400,
)
# fig2 = px.scatter(df_raw, x='yaw_abs', y='face_quality', template='ggplot2', trendline='ols')
# fig2.update_layout(
#     width=500,
#     height=500,
#     xaxis_title="Absolute Yaw angle",
# )
fig.write_image("figures/face_quality_two_three_people_box.png")
dfs1['Subjects'] = 2
dfs2['Subjects'] = 3
dfs = pd.concat([dfs1, dfs2], axis=0)
dfs = dfs.round(3).drop(columns=['std', 'median'])
# drop rows where subset (index) ends with _diff
dfs = dfs[~dfs.index.str.startswith('base')]
dfs.index = dfs.index.map(rename_dict)
dfs

mean  stderr  Subjects
subset                                                 
IPAdapter Plus FaceID v2        0.819   0.003         2
FaceID No Face Inpaint          0.769   0.004         2
IPAdapter Plus Face             0.787   0.004         2
IPAdapter Plus No Face Inpaint  0.766   0.005         2
IPAdapter Plus FaceID v2        0.816   0.003         3
FaceID No Face Inpaint          0.751   0.004         3
IPAdapter Plus Face             0.787   0.004         3
IPAdapter Plus No Face Inpaint  0.740   0.005         3

# Head position

In [86]:
from functools import partial

In [87]:
def bootstrap_standard_error(data, f, num_bootstraps=1000):
    n = len(data)
    bootstrap_estimates = np.zeros(num_bootstraps)
    
    for i in range(num_bootstraps):
        # Generate a bootstrap sample
        bootstrap_sample = np.random.choice(data, size=n, replace=True)
        
        # Calculate the metric for this bootstrap sample
        bootstrap_estimates[i] = f(bootstrap_sample)
    
    # Calculate the standard error
    return np.std(bootstrap_estimates)

In [101]:
def get_std_difference(experiments: list, experiment_ref: str | list, remove_numbering=False):
    for s in experiments:
        if not subset_exists(s):
            print(f"Subset {s} does not exist")
    if type(experiment_ref) == str:
        experiment_ref = [experiment_ref]
    for ref in experiment_ref:
        if ref not in experiments:
            raise ValueError(f"Reference experiment {ref} not in experiments")
    df_raw = pd.concat(
        [
            get_dataframe_faces(subset_name)[['subset', 'pitch', 'yaw', 'roll']]
            for subset_name in experiments
        ],
        axis=0,
    )
    if remove_numbering:
        df_raw['subset'] = df_raw['subset'].map(rename_dict)
    df_ref = pd.concat([get_dataframe_faces(ref) for ref in experiment_ref], axis=0)
    std_diff_pitch = df_raw.groupby('subset')['pitch'].agg([
        # ('pitch_mean', 'mean'),
        ('pitch_std', 'std'),
        ('pitch_wasserstein', lambda x: wasserstein_distance(df_ref['pitch'], x)),
        ('pitch_wass_se', lambda x: bootstrap_standard_error(x, partial(wasserstein_distance, df_ref['pitch'])))
    ])
    std_diff_yaw = df_raw.groupby('subset')['yaw'].agg([
        # ('yaw_mean', 'mean'),
        ('yaw_std', 'std'),
        ('yaw_wasserstein', lambda x: wasserstein_distance(df_ref['yaw'], x)),
        ('yaw_wass_se', lambda x: bootstrap_standard_error(x, partial(wasserstein_distance, df_ref['yaw'])))
    ])
    std_diff_roll = df_raw.groupby('subset')['roll'].agg([
        # ('roll_mean', 'mean'),
        ('roll_std', 'std'),
        ('roll_wasserstein', lambda x: wasserstein_distance(df_ref['roll'], x)),
        ('roll_wass_se', lambda x: bootstrap_standard_error(x, partial(wasserstein_distance, df_ref['roll'])))
    ])
    std_diff = pd.concat([std_diff_pitch, std_diff_yaw, std_diff_roll], axis=1)
    return std_diff, df_raw

In [94]:
def get_face_positions(experiments_face_positions: list, title: str):
    for s in experiments_face_positions:
        if not subset_exists(s):
            print(f"Subset {s} does not exist")
    df_raw = pd.concat(
        [
            get_dataframe_faces(subset_name)
            for subset_name in experiments_face_positions
        ],
        axis=0,
    )
    # df_melted = pd.melt(df_raw, 
    #                     id_vars=['subset'], 
    #                     value_vars=['pitch', 'yaw', 'roll'],
    #                     var_name='face_position',
    #                     value_name='angle')

    # Update the layout
    figs = []
    for p in ['pitch', 'yaw', 'roll']:
        hist_data = [df_raw[df_raw['subset'] == s][p] for s in experiments_face_positions]
        fig_hist = ff.create_distplot(hist_data, experiments_face_positions, bin_size=.2, show_hist=False, show_rug=False, colors=ggplot_colors)
        fig_hist.update_layout(
            template='ggplot2',
            yaxis_title="Density",
            xaxis_title="Degrees",
            title=f"{p} distribution per method",
            xaxis=dict(
                title=dict(font=dict(size=16)),
                tickfont=dict(size=14),
                range=[-100, 100]
            ),
            yaxis=dict(
                title=dict(font=dict(size=16)),
                tickfont=dict(size=14)
            ),
            legend_title_text='Method',
            width=800,
            height=400
        )
        figs.append(fig_hist)
    return figs

In [95]:
experiments_two = [
    "two_people_faceid_dreamshaper",
    "two_people_normalip",
    "base_two_people_dreamshaper+face",
    "base_two_people_dreamshaper+face_newseed"
]
experiments_three = [
    "three_people_faceid_dreamshaper",
    "three_people_normalip",
    "base_three_people_dreamshaper+face",
    "base_three_people_dreamshaper+face_newseed"
]

In [96]:
figs2 = get_face_positions(experiments_two, title="Face Position per method for two people generation")
figs3 = get_face_positions(experiments_three, title="Face Position per method for three people generation")
fig_all = make_subplots(rows=3, cols=2, 
                        subplot_titles=("Two People Pitch", "Three People Pitch", "Two People Yaw", "Three People Yaw", "Two People Roll", "Three People Roll"),
                        horizontal_spacing=0.08, 
                        vertical_spacing=0.1)
for r, fig in enumerate(figs2, 1):
    for trace in fig['data']:
        fig_all.add_trace(trace, row=r, col=1)
for r, fig in enumerate(figs3, 1):
    for trace in fig['data']:
        fig_all.add_trace(trace, row=r, col=2)
# Update layout for a single legend
fig_all.update_layout(
    height=900,  # Increased height to accommodate more subplots
    width=900,
    template='ggplot2',
    title=dict(
        text="",
        y=0.98,
        x=0.5,
        xanchor='center',
        yanchor='top'
    ),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    margin=dict(l=20, r=20, t=100, b=50)
)
for r in [1, 2, 3]:
    for c in [1,2]:
        fig_all.update_xaxes(range=[-70, 70], row=r, col=c)
        fig_all.update_traces(showlegend=False, row=r, col=c)
fig_all.update_xaxes(title_text='Angle Degree', row=3, col=1)
fig_all.update_xaxes(title_text='Angle Degree', row=3, col=2)
legend_items = ["IPAdapter Plus FaceID v2", "IPAdapter Plus Face", "Prompt Only", "Prompt Only (New Seed)"]
l = 0
for i, (item, color) in enumerate(zip(legend_items, ggplot_colors)):
    n_chars = len(item)
    fig_all.add_shape(type="line",
        xref="paper", yref="paper",
        x0=0.03 + l, y0=1.1,
        x1=0.06 + l, y1=1.1,
        line=dict(color=color, width=4)
    )
    fig_all.add_annotation(
        xref="paper", yref="paper",
        x=0.065 + l, y=1.1,
        text=item,
        showarrow=False,
        xanchor="left",
        yanchor="middle"
    )
    l += n_chars * 0.009 + 0.05
# for i in range(2):
#     fig_all.layout.annotations[i].update(y=1.05, font_size=16)
fig_all.show()
fig_all.write_image("figures/face_positions.png")

/var/folders/yk/cdtxd1bs4ll60mb745f9lg4w0000gn/T/ipykernel_87065/3826901117.py:5: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

/var/folders/yk/cdtxd1bs4ll60mb745f9lg4w0000gn/T/ipykernel_87065/3826901117.py:5: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [99]:
experiments_two = [
    "two_people_faceid_dreamshaper",
    "two_people_faceid_no_controlnet",
    "two_people_normalip",
    "two_people_normalip_no_controlnet",
    "base_two_people_dreamshaper+face",
    "base_two_people_dreamshaper+face_newseed"
]
experiments_three = [
    "three_people_faceid_dreamshaper",
    "three_people_faceid_no_controlnet",
    "three_people_normalip_no_controlnet",
    "three_people_normalip",
    "base_three_people_dreamshaper+face",
    "base_three_people_dreamshaper+face_newseed"
]
wass_2, df_raw2 = get_std_difference(experiments_two, "base_two_people_dreamshaper+face")
wass_3, df_raw3 = get_std_difference(experiments_three, "base_three_people_dreamshaper+face")
display(wass_2)
for e in [wass_2, wass_3]:
    # rename subset values using rename_dict
    e.index = e.index.map(rename_dict)
    # e.drop(columns=['pitch_mean', 'pitch_std', 'yaw_mean', 'yaw_std', 'roll_mean', 'roll_std'], axis=1, inplace=True)
    # drop rows with subset (index) euqal to reference experiment
    e.drop(index='Prompt Alone', inplace=True)
    # remove rows that end with _diff
wass_2['Subjects'] = 2
wass_3['Subjects'] = 3
wass = pd.concat([wass_2, wass_3], axis=0)
# wass = wass.round(3).drop(columns=['pitch_mean', 'yaw_mean', 'roll_mean'], axis=1)
wass.reset_index(inplace=True)
# wass = wass.iloc[:, [7, 0, 1, 2, 3,4, 5,6]]
wass.round(2)

pitch_std  pitch_wasserstein  \
subset                                                                   
base_two_people_dreamshaper+face          21.907532           0.000000   
base_two_people_dreamshaper+face_newseed  20.219941           1.112993   
two_people_faceid_dreamshaper             15.113181           7.338739   
two_people_faceid_no_controlnet           12.959250           9.621057   
two_people_normalip                       12.723866           9.892533   
two_people_normalip_no_controlnet         11.049812          12.798658   

                                          pitch_wass_se    yaw_std  \
subset                                                               
base_two_people_dreamshaper+face               0.309093  43.405402   
base_two_people_dreamshaper+face_newseed       0.311255  43.136570   
two_people_faceid_dreamshaper                  0.395677  32.402405   
two_people_faceid_no_controlnet                0.332131  27.734744   
two_people_normalip                            0.305329  26.910201   
two_people_normalip_no_controlnet              0.303296  20.921519   

                                          yaw_wasserstein  yaw_wass_se  \
subset                                                                   
base_two_people_dreamshaper+face                 0.000000     0.678172   
base_two_people_dreamshaper+face_newseed         3.649508     1.150994   
two_people_faceid_dreamshaper                   11.112869     0.650593   
two_people_faceid_no_controlnet                 15.897991     0.582890   
two_people_normalip                             16.992530     0.595916   
two_people_normalip_no_controlnet               24.941593     0.556905   

                                           roll_std  roll_wasserstein  \
subset                                                                  
base_two_people_dreamshaper+face          26.213790          0.000000   
base_two_people_dreamshaper+face_newseed  24.979569          2.328815   
two_people_faceid_dreamshaper             18.952675          6.055623   
two_people_faceid_no_controlnet           15.430403          9.146492   
two_people_normalip                       17.315126          7.272587   
two_people_normalip_no_controlnet         13.691497         10.636061   

                                          roll_wass_se  
subset                                                  
base_two_people_dreamshaper+face              0.383436  
base_two_people_dreamshaper+face_newseed      0.635028  
two_people_faceid_dreamshaper                 0.418803  
two_people_faceid_no_controlnet               0.354076  
two_people_normalip                           0.374641  
two_people_normalip_no_controlnet             0.325615

In [104]:
# ablation
experiments = [
    "two_people_faceid_dreamshaper",
    "base_two_people_dreamshaper+face",
    "two_people_faceid_no_controlnet",
    "two_people_normalip",
    "two_people_normalip_no_controlnet",
    "three_people_faceid_dreamshaper",
    "base_three_people_dreamshaper+face",
    "three_people_faceid_no_controlnet",
    "three_people_normalip_no_controlnet",
    "three_people_normalip",
]
wass, df_raw = get_std_difference(experiments, ["base_two_people_dreamshaper+face", "base_three_people_dreamshaper+face"], remove_numbering=True)
display(wass.round(2))
# wassmstd = wass.round(3)

pitch_std  pitch_wasserstein  pitch_wass_se  \
subset                                                                  
IPA+ FIDv2 No ControlNet      13.87               8.36           0.24   
IPA+ Face No ControlNet       10.64              11.47           0.18   
IPAdapter Plus Face           12.58               8.80           0.21   
IPAdapter Plus FaceID v2      14.73               6.89           0.25   
Prompt Alone                  21.41               0.00           0.19   

                          yaw_std  yaw_wasserstein  yaw_wass_se  roll_std  \
subset                                                                      
IPA+ FIDv2 No ControlNet    27.17            13.92         0.40     15.98   
IPA+ Face No ControlNet     21.84            21.15         0.37     13.41   
IPAdapter Plus Face         27.11            14.30         0.40     16.74   
IPAdapter Plus FaceID v2    30.99            10.05         0.42     18.19   
Prompt Alone                41.13             0.00         0.39     24.77   

                          roll_wasserstein  roll_wass_se  
subset                                                    
IPA+ FIDv2 No ControlNet              7.41          0.25  
IPA+ Face No ControlNet               8.93          0.21  
IPAdapter Plus Face                   6.04          0.25  
IPAdapter Plus FaceID v2              5.27          0.27  
Prompt Alone                          0.00          0.22

In [80]:
df_raw2.groupby('subset').count()

pitch  yaw  roll
subset                                            
base_two_people_dreamshaper+face    950  950   950
two_people_faceid_dreamshaper       918  918   918
two_people_normalip                 919  919   919

 # Bbox size distribution

In [108]:
experiments = [
    "two_people_faceid_dreamshaper",
    "two_people_faceid_no_controlnet",
    "two_people_normalip",
    "two_people_normalip_no_controlnet",
    "three_people_faceid_dreamshaper",
    "three_people_faceid_no_controlnet",
    "three_people_normalip_no_controlnet",
    "three_people_normalip",
]
df = pd.concat(
    [
        get_dataframe_faces(subset_name)[['subset', 'bbox_size']]
        for subset_name in experiments
    ],
    axis=0,
)
df['subset'] = df['subset'].map(rename_dict)
df['bbox_sqrt'] = df['bbox_size'].apply(np.sqrt)

In [110]:
df.head()

subset  bbox_size   bbox_sqrt
0  IPAdapter Plus FaceID v2    10502.0  102.479266
1  IPAdapter Plus FaceID v2    11640.0  107.888832
3  IPAdapter Plus FaceID v2    10043.0  100.214769
4  IPAdapter Plus FaceID v2     9520.0   97.570487
5  IPAdapter Plus FaceID v2     5655.0   75.199734

In [115]:
fig = px.box(df, y='bbox_sqrt', x='subset', template='ggplot2')
fig.update_layout(
    width=500,
    height=500,
)

# CLIP scores - Ablation study Face Matching, control net

In [11]:
def get_clip_scores(experiments: list):
    for s in experiments:
        if not subset_exists(s):
            print(f"Subset {s} does not exist")
    df_raw = pd.concat(
        [
            construct_dataframe(subset_name)
            for subset_name in experiments
        ],
        axis=0,
    )
    dfs = df_raw.groupby('subset')['clip_score'].agg([
    ('mean', 'mean'),
    ('std', 'std'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
    ])
    fig_box = px.box(df_raw, y="clip_score", x="subset", 
                     template='ggplot2',
                     width=800, height=400)
    fig_box.update_layout(
        yaxis_title="CLIP Score",
        xaxis_title="Method",
        title="CLIP score per method",
        xaxis=dict(
            title=dict(font=dict(size=16)),
            tickfont=dict(size=14),
            tickmode='array',
            tickvals=[0, 1],  # Position of tick marks
            ticktext=['IPAdapter Plus FaceID v2', 'IPAdapter Plus Face']  # Labels for tick marks
        ),
        yaxis=dict(
            title=dict(font=dict(size=16)),
            tickfont=dict(size=14),
        )
    )
    return fig_box, dfs, df_raw

In [12]:
experiments_two = [
    "child_adult_faceid",
    "child_adult_faceid_no_facematch",
    "child_adult_normalip",
    "child_adult_normalip_no_facematch",
    "man_woman_faceid",
    "man_woman_faceid_rev_facematch",
    "man_woman_normalip",
    "man_woman_normalip_rev_facematch"
]
fig1, dfs1, df_raw1 = get_clip_scores(experiments_two)
df_raw1['no_facematch'] = df_raw1['subset'].str.contains('facematch')
df_raw1['subset'] = df_raw1['subset'].str.replace('_no_facematch', '')
df_raw1['subset'] = df_raw1['subset'].str.replace('_rev_facematch', '')
fig = px.box(df_raw1, x='subset', y='clip_score', color='no_facematch', template='ggplot2')
fig.update_layout(
    xaxis_title="Method",
    yaxis_title="CLIP score",
    width=800,
    height=400,
)
fig.show()
display(dfs1.drop(columns=['std']).round(3))

/var/folders/yk/cdtxd1bs4ll60mb745f9lg4w0000gn/T/ipykernel_24160/2073468642.py:5: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



mean  stderr
subset                                           
child_adult_faceid                 36.189   0.123
child_adult_faceid_no_facematch    35.160   0.115
child_adult_normalip               36.225   0.125
child_adult_normalip_no_facematch  35.054   0.116
man_woman_faceid                   36.055   0.119
man_woman_faceid_rev_facematch     35.385   0.117
man_woman_normalip                 36.111   0.123
man_woman_normalip_rev_facematch   35.366   0.121

In [63]:
# ablation
experiments = [
    "two_people_faceid_dreamshaper",
    "two_people_normalip",
    "two_people_faceid_no_controlnet",
    "two_people_normalip_no_controlnet",
    "three_people_faceid_dreamshaper",
    "three_people_normalip",
    "three_people_faceid_no_controlnet",
    "three_people_normalip_no_controlnet",
]
fig1, dfs1, df_raw1 = get_clip_scores(experiments)
display(dfs1)
# drop rows where subset (index) ends with _diff
df_raw1['subset'] = df_raw1['subset'].map(rename_dict)
df_raw1.groupby('subset')[['clip_score']].agg([
    ('mean', 'mean'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
]).round(3)

mean       std    stderr
subset                                                            
three_people_faceid_dreamshaper      38.384995  3.009373  0.134583
three_people_faceid_no_controlnet    38.066925  2.862859  0.128031
three_people_normalip                38.228744  3.047815  0.136302
three_people_normalip_no_controlnet  38.564685  2.985457  0.133514
two_people_faceid_dreamshaper        38.408154  2.962055  0.132467
two_people_faceid_no_controlnet      38.134699  2.906460  0.129981
two_people_normalip                  38.348992  3.014159  0.134797
two_people_normalip_no_controlnet    38.724891  3.027150  0.135378

clip_score       
                               mean stderr
subset                                    
IPA+ FIDv2 No ControlNet     38.101  0.091
IPA+ Face No ControlNet      38.645  0.095
IPAdapter Plus Face          38.289  0.096
IPAdapter Plus FaceID v2     38.397  0.094

In [20]:
import numpy as np
from scipy import stats

In [21]:
df_raw1.head()

subset  image_id  clip_score quality natural  n_people_front  \
0  child_adult_faceid         0   36.860569    None    None               0   
1  child_adult_faceid         1   37.383194    None    None               0   
2  child_adult_faceid         2   37.347286    None    None               0   
3  child_adult_faceid         3   35.537956    None    None               0   
4  child_adult_faceid         4   38.689468    None    None               0   

   facematch  
0      False  
1      False  
2      False  
3      False  
4      False

In [22]:
sample2 = df_raw1[df_raw1.subset == 'child_adult_normalip']['clip_score']
sample1 = df_raw1[df_raw1.subset == 'child_adult_normalip_no_facematch']['clip_score']
t_statistic, p_value = stats.ttest_ind(sample1, sample2, alternative='less')
print(f"T-statistic: {t_statistic}")
print(f"P-value: {p_value}")

T-statistic: nan
P-value: nan


/var/folders/yk/cdtxd1bs4ll60mb745f9lg4w0000gn/T/ipykernel_87065/790166889.py:3: SmallSampleWarning:

One or more sample arguments is too small; all returned values will be NaN. See documentation for sample size requirements.



In [23]:
fig = px.bar(dfs1.reset_index(), x="subset", y="mean", template='ggplot2', error_y='stderr')
fig.update_layout(
    width=800,
    height=500,
)
fig.show()

# CLIP-IQA

In [24]:
def get_clipiqa_scores(experiments: list):
    for s in experiments:
        if not subset_exists(s):
            print(f"Subset {s} does not exist")
    df_raw = pd.concat(
        [
            construct_dataframe(subset_name)
            for subset_name in experiments
        ],
        axis=0,
    )
    dfs = df_raw.groupby('subset')[['quality', 'natural']].agg([
    ('mean', 'mean'),
    ('std', 'std'),
    ('stderr', lambda x: x.std() / np.sqrt(x.count()))
    ])
    return dfs

In [25]:
experiments_two = [
    "two_people_faceid_dreamshaper",
    "two_people_normalip",
    "base_two_people_dreamshaper+face",
    "two_people_faceid_no_facematch",
    "child_adult_faceid",
    "child_adult_faceid_no_facematch",
    "child_adult_normalip",
    "child_adult_normalip_no_facematch"
]
experiments_three = [
    "three_people_faceid_dreamshaper",
    "three_people_normalip",
    "base_three_people_dreamshaper+face",
    "three_people_faceid_no_facematch"
]
dfs1 = get_clipiqa_scores(experiments_two)
dfs2 = get_clipiqa_scores(experiments_three)
for dd in [dfs1, dfs2]:
    # dd.index = dd.index.map(rename_dict)
    dd.drop(columns=[('quality', 'std'), ('natural', 'std')], axis=1, inplace=True)
    dd.columns = ['_'.join(col).strip() for col in dd.columns.values]
dfs1['n_people'] = 2
dfs2['n_people'] = 3
dfs = pd.concat([dfs1, dfs2], axis=0)
dfs

/var/folders/yk/cdtxd1bs4ll60mb745f9lg4w0000gn/T/ipykernel_87065/3889091068.py:5: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



quality_mean  quality_stderr  \
subset                                                             
base_two_people_dreamshaper+face        0.951995        0.002064   
child_adult_faceid                           NaN             NaN   
child_adult_faceid_no_facematch              NaN             NaN   
child_adult_normalip                         NaN             NaN   
child_adult_normalip_no_facematch            NaN             NaN   
two_people_faceid_dreamshaper           0.949405        0.002199   
two_people_faceid_no_facematch          0.949391        0.002139   
two_people_normalip                     0.945749        0.002382   
base_three_people_dreamshaper+face      0.949293        0.002405   
three_people_faceid_dreamshaper         0.952423        0.002055   
three_people_faceid_no_facematch        0.950726        0.002245   
three_people_normalip                   0.945180        0.002387   

                                    natural_mean  natural_stderr  n_people  
subset                                                                      
base_two_people_dreamshaper+face        0.875430        0.006886         2  
child_adult_faceid                           NaN             NaN         2  
child_adult_faceid_no_facematch              NaN             NaN         2  
child_adult_normalip                         NaN             NaN         2  
child_adult_normalip_no_facematch            NaN             NaN         2  
two_people_faceid_dreamshaper           0.901028        0.006081         2  
two_people_faceid_no_facematch          0.902329        0.005870         2  
two_people_normalip                     0.902273        0.005951         2  
base_three_people_dreamshaper+face      0.858591        0.007146         3  
three_people_faceid_dreamshaper         0.888825        0.006128         3  
three_people_faceid_no_facematch        0.888540        0.006101         3  
three_people_normalip                   0.891836        0.005948         3

In [26]:
    dfs1.columns

Index(['quality_mean', 'quality_stderr', 'natural_mean', 'natural_stderr',
       'n_people'],
      dtype='object')

}# People Count

In [27]:
df1 = construct_dataframe("base_one_person_dreamshaper")
df2 = construct_dataframe("base_two_people_dreamshaper")
df3 = construct_dataframe("base_three_people_dreamshaper")
df4 = construct_dataframe("base_four_people_dreamshaper")
dfs = {
    1: df1,
    2: df2,
    3: df3,
    4: df4
}
df1.head(2)

subset  image_id  clip_score   quality   natural  \
0  base_one_person_dreamshaper         0   40.556099  0.963395  0.841794   
1  base_one_person_dreamshaper         1   38.653530  0.927488  0.784836   

   n_people_front  
0               1  
1               1

In [28]:
for target_num, df in dfs.items():
    df['people_diff'] = df['n_people_front'] - target_num

In [29]:
df1.groupby('people_diff')

In [30]:
fig1 = px.histogram(df1, x='n_people_front', 
                     template='ggplot2',
                     width=650, height=350)
fig2 = px.histogram(df2, x='n_people_front', 
                     template='ggplot2',
                     width=650, height=350)
fig3 = px.histogram(df3, x='n_people_front',
                        template='ggplot2',
                        width=650, height=350)
fig4 = px.histogram(df4, x='n_people_front',
                        template='ggplot2',
                        width=650, height=350)
figs = [fig1, fig2, fig3, fig4]
for i, f in enumerate(figs, 1):
    f.update_layout(
        xaxis_title="Number of generated people",
        title_text=f"{i} people generation",
    )
fig1.update_layout(
    title_text="One person generation",
)
fig4.update_layout(
    xaxis=dict(
        tickmode='array',
        tickvals=[0, 1, 2, 3, 4, 5, 6,7,8,9],
        ticktext=['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']
    )
)
fig1.show()
fig2.show()
fig3.show()
fig4.show()
fig1.write_image("people_count_one_person.png")
fig2.write_image("people_count_two_people.png")
fig3.write_image("people_count_three_people.png")
fig4.write_image("people_count_four_people.png")

In [31]:
display(df1['people_diff'].value_counts().sort_index())
display(df2['people_diff'].value_counts().sort_index())
display(df3['people_diff'].value_counts().sort_index())
display(df4['people_diff'].value_counts().sort_index())

people_diff
-1      4
 0    484
 1     10
 3      1
 4      1
Name: count, dtype: int64

people_diff
-2      2
-1     22
 0    399
 1     74
 2      3
Name: count, dtype: int64

people_diff
-3      5
-2     13
-1     71
 0    300
 1     99
 2     10
 3      2
Name: count, dtype: int64

people_diff
-4      1
-3      4
-2     40
-1    259
 0    161
 1     29
 2      4
 4      1
 5      1
Name: count, dtype: int64